![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Komputerowe wspomaganie tłumaczenia </h1>
<h2> 1. <i>Podstawowe techniki wspomagania tłumaczenia</i> [laboratoria]</h2> 
<h3>Rafał Jaworski (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Podstawowy scenariusz - tłumacz otrzymuje **dokument** będący ciągiem **segmentów** w **języku źródłowym** . Zadaniem tłumacza jest przetłumaczenie wszystkich segmentów na **język docelowy**. Oznacza to, że został wykonany już szereg operacji technicznych, a w tym:
- przesłanie pliku do tłumaczenia
- ekstrakcja tekstu z dokumentu
- podział tekstu na segmenty.


Tłumacz tłumaczy jeden segment na raz. Widzi kilka poprzednich oraz kilka następnych segmentów, jednak jego uwaga powinna skupiać się na aktywnym, aktualnie tłumaczonym segmencie. Nie oznacza to jednak, że tłumacz jest pozbawiony pomocy. Ma możliwość korzystania z różnorakich technik **komputerowego wspomagania tłumaczenia**.

# Pamięć tłumaczeń

Najbardziej podstawową techniką wspomagania tłumaczenia jest **pamięć tłumaczeń**. Pamięć tłumaczeń stanowi zbiór wcześniej przetłumaczonych zdań:

In [2]:
translation_memory = [('Wciśnij przycisk Enter', 'Press the ENTER button'), 
                      ('Sprawdź ustawienia sieciowe', 'Check the network settings')]

Kiedy tłumacz pracuje nad kolejnym zdaniem, program automatycznie przeszukuje pamięć tłumaczeń. Jeśli okaże się, że zdanie zostało już przetłumaczone, automatycznie pobierane jest jego tłumaczenie z pamięci:

In [3]:
def tm_lookup(sentence):
    return [entry[1] for entry in translation_memory if entry[0] == sentence]

In [4]:
tm_lookup('Wciśnij przycisk Enter')

['Press the ENTER button']

W takim przypadku tłumaczenie z pamięci jest najczęściej automatycznie wstawiane jako tłumaczenie segmentu źródłowego i tłumacz nie musi się już nim martwić (co więcej, nie dostaje za takie tłumaczenie zapłaty...)

Tłumacz pracuje dalej i każde wykonane przez niego tłumaczenie trafia do pamięci tłumaczeń (oczywiście dzieje się to automatycznie):

In [5]:
translation_memory.append(('Drukarka jest wyłączona', 'The printer is switched off'))
translation_memory.append(('Wymagane ponowne uruchomienie komputera', 'System restart required'))
translation_memory.append(('Wciśnij przycisk Enter', 'Press the ENTER key'))

Z całą pewnością tłumacz stara się przełożyć jakąś komputerową instrukcję. Po wielu godzinach pracy trafia na znane sobie zdanie "Wciśnij przycisk Enter". Następuje przeszukanie pamięci tłumaczeń:

In [6]:
tm_lookup('Wciśnij przycisk Enter')

['Press the ENTER button', 'Press the ENTER key']

Jak widać, mamy w pamięci dwa tłumaczenia tego zdania. To tłumacz musi zadecydować, które tłumaczenie wybrać. O metodach wspomagania decyzji tłumacza w takich przypadkach będziemy jeszcze mówić.

Przeanalizujmy teraz następujący przypadek: do tłumaczenia trafia zdanie: "Wciśnij przycisk ENTER":

In [9]:
tm_lookup('Wciśnij przycisk ENTER')

[]

Tutaj tłumacz nie ma szczęścia - restrykcyjny mechanizm wyszukiwania nie podaje mu podpowiedzi. Możemy jednak sprawić, żeby przeszukiwanie pamięci tłumaczeń nie brało pod uwagę wielkości liter.

### Ćwiczenie 1: zmodyfikuj funkcję tm_lookup w taki sposób, aby nie brała pod uwagę wielkości liter. Przetestuj zmodyfikowaną funkcję.

In [11]:
def tm_lookup(sentence):
    return [entry[1] for entry in translation_memory if entry[0].lower() == sentence.lower()]

tm_lookup('Wciśnij przycisk ENTER')

['Press the ENTER button', 'Press the ENTER key']

Nasz tłumacz powinien być teraz zadowolony. Jednak w dalszej części dokumentu pojawiło się inne podobne zdanie, dla którego nie było tłumaczenia:

In [8]:
tm_lookup('Wciśnij przycisk [ENTER]')

[]

### Ćwiczenie 2: zmodyfikuj funkcję tm_lookup w taki sposób, aby nie brała pod uwagę znaków interpunkcyjnych. Rada - zdefiniuj funkcję sentence_similar.

In [16]:
import string

def tm_lookup(sentence):
    sentence = sentence.translate(str.maketrans('', '', string.punctuation))
    return [entry[1] for entry in translation_memory if entry[0].lower() == sentence.lower()]

tm_lookup('Wciśnij przycisk [ENTER]')

['Press the ENTER button', 'Press the ENTER key']

Praca tłumacza oczywiście trwa nadal. Spróbujmy teraz zaradzić następującej sytuacji - tłumacz otrzymuje do tłumaczenia następujące zdanie:

In [17]:
tm_lookup('Wymagane ponowne uruchomienie maszyny')

[]

Znów nie otrzymuje od nas podpowiedzi i znów nic w tym dziwnego - w pamięci tłumaczeń nie znajduje się takie zdanie. Jest jednak zdanie podobne, różniące się jednym słowem.

### Ćwiczenie 3: zmodyfikuj funkcję tm_lookup w taki sposób, aby zwracała podpowiedzi także wtedy, gdy zdania różnią się tylko jednym słowem.

In [26]:
def differenceThanNotBiggerThanOneElement(firstSentence, secondSentence):
   firstSentenceList = firstSentence.lower().split()
   secondSentenceList = secondSentence.lower().split()

   diffNumber = 0

   for i in range(len(firstSentenceList)):
       if(firstSentenceList[i] != secondSentenceList[i]):
           diffNumber=diffNumber+1
           if(diffNumber > 2):
               return False

   return True

def tm_lookup(sentence):
    sentence = sentence.translate(str.maketrans('', '', string.punctuation))

    exactMatchList = [entry[1] for entry in translation_memory if entry[0].lower() == sentence.lower()]

    if(len(exactMatchList) == 0):
      diffMatchList =  [entry[1] for entry in translation_memory if differenceThanNotBiggerThanOneElement(entry[0], sentence)]

      if(len(diffMatchList) > 0):
        print('Suggestion:')
        return diffMatchList

    else:
        return exactMatchList






   

tm_lookup('Wymagane ponowne uruchomienie maszyny')

Suggestion:


['System restart required']

# Słownik kontekstowy / glosariusz

Inną podstawową pomocą dla naszego tłumacza jest słownik, zwany także glosariuszem. Stanowi on zbiór terminów w języku źródłowym wraz z ich tłumaczeniami na język docelowy:

In [27]:
glossary = [('komputer', 'computer'), ('przycisk', 'button'), ('drukarka', 'printer')]

Podczas tłumaczenia, glosariusz jest przeszukiwany w celu znalezienia aktualnie tłumaczonych słów.

In [28]:
def glossary_lookup(sentence):
    sentence_words = sentence.split()
    return [entry for entry in glossary if entry[0] in sentence_words]

In [29]:
glossary_lookup('Każda drukarka posiada przycisk wznowienia drukowania')

[('przycisk', 'button'), ('drukarka', 'printer')]

### Ćwiczenie 4: (tym razem teoretyczne) Jaka jest złożoność obliczeniowa czasowa przedstawionego powyżej algorytmu względem liczby haseł w słowniku (n) oraz liczby słów w zdaniu do tłumaczenia (m)?

Odpowiedź: O(n * m)

### Ćwiczenie 5: zmodyfikuj funkcję glossary_lookup w taki sposób, aby nie brała pod uwagę wielkości liter.

In [34]:
def glossary_lookup(sentence):
    sentence_words = sentence.lower().split()
    return [entry for entry in glossary if entry[0] in sentence_words]

glossary_lookup('Każda Drukarka posiada Przycisk wznowienia drukowania')

[]

### Ćwiczenie 6: zmodyfikuj funkcję glossary_lookup w taki sposób, aby jej złożoność obliczeniowa była mniejsza.

In [35]:
def glossary_lookup(sentence):
    sentence_words = set(sentence.lower().split())
    return [entry for entry in glossary if entry[0] in sentence_words]

glossary_lookup('Każda Drukarka posiada Przycisk wznowienia drukowania')

[('przycisk', 'button'), ('drukarka', 'printer')]